## Geographical demand patterns
In this notebook, we will explore geographical demand patterns, also through visualization of points of interest. Furthermore, we will determine the correlation between different points of interest and demand for bicycles and have a look at spatio-temporal demand patterns.

In [28]:
import pandas as pd
import folium
from folium import plugins
from folium.plugins import HeatMap
import h3
import import_ipynb
import H3_Visualization
from datetime import datetime

In [19]:
trips_df = pd.read_pickle("../00_data/trips.pkl")
stations_df = pd.read_pickle("../00_data/stations.pkl")
hexagons_df = pd.read_pickle("../00_data/hexagons.pkl")
poi_df = pd.read_pickle("../00_data/poi.pkl")

First of all, we will create a heatmap representing all started trips and also mark bike stations on the same map. This should provide us with a rough overview of which areas in Los Angeles have high demand (i.e. are most or least popular to start the trip).

In [20]:
# add joint coordinates column to plot heatmap
trips_df["start_coordinates"] = list(
    zip(trips_df["start_latitude"].round(4), trips_df["start_longitude"].round(4))
)
trips_df["end_coordinates"] = list(
    zip(trips_df["end_latitude"].round(4), trips_df["end_longitude"].round(4))
)

stations_df["coordinates"] = list(
    zip(stations_df["latitude"].round(4), stations_df["longitude"].round(4))
)

In [21]:
# plot heatmap for starting trips
trips_heatmap = folium.Map(
    location=(34.052235, -118.447),
    tiles="Stamen Toner",
    zoom_start=11,
    control_scale=True,
    max_zoom=20,
)

trips_heatmap.add_child(plugins.HeatMap(trips_df["start_coordinates"], radius=30))

for position in stations_df["coordinates"]:
    folium.CircleMarker(
        radius=5,
        location=position,
        popup="The Waterfront",
        color="crimson",
        fill_color="crimson",
    ).add_to(trips_heatmap)
trips_heatmap

The heatmap shows areas of higher and lower popularity. The wider circle around Santa Monica seems to have no trips at all. These stations were probably introduced later because our trip data is from 2019 and stations data from 2021.

However, due to a large amount of data, it is difficult to compare different areas between each other. For example, it would be difficult to determine whether Burbank experiences more demand than upper Los Angeles. Therefore, we will use h3 geospatial indexing system introduced in /01_data_collection_and_preparation/04_poi.ipynb. By filling the hexagons with different intensity colors we will be able to compare demand in these hexagons.

In [22]:
# this function will count trips for a given 'group by' value
def calculate_hexagon_trips(label, group_by):
    hexagons_df[label] = trips_df.groupby(group_by).size()
    hexagons_df[label] = hexagons_df[label].fillna(value=0)

In [29]:
# geometry is required to plot hexagons
hexagons_df["geometry"] = hexagons_df.apply(H3_Visualization.add_geometry, axis=1)

AttributeError: module 'H3_Visualization' has no attribute 'add_geometry'

In [24]:
# calculate incoming and outgoing trips for each hexagon
hexagons_df = hexagons_df.set_index("hex")

calculate_hexagon_trips(label="incoming_trips", group_by="start_hex")
calculate_hexagon_trips(label="outgoing_trips", group_by="end_hex")

hexagons_df = hexagons_df.reset_index()
hexagons_df.head(2)

hex                                  hex_and_neighbors  \
0  8929a1d7577ffff  [8929a1d7573ffff, 8929a1d7563ffff, 8929a1d750f...   
1  8929a1d7543ffff  [8929a1d7547ffff, 8929a1d755bffff, 8929a1d7543...   

   sustenance_poi  public_transport_poi  education_poi  arts_and_culture_poi  \
0              80                    28              2                     4   
1              40                     1              2                     0   

   sports_poi  incoming_trips  outgoing_trips  
0           0           12804           11124  
1           1            3473            3530

In [25]:
# this function will return hex id for given latitude and longitude
def convert_to_hex(latitude, longitude):
    return h3.geo_to_h3(lat=latitude, lng=longitude, resolution=9)

In [26]:
# compute hex id for each station and merge with the hexagons data afterwards
stations_df["hex"] = stations_df.apply(
    lambda station: convert_to_hex(station["latitude"], station["longitude"]), axis=1
)
stations_df = pd.merge(stations_df, hexagons_df, left_on="hex", right_on="hex")
stations_df.head(2)


latitude  longitude zip_code  total_docks  is_event_based  is_virtual  \
0  34.04850 -118.25854    90017           31           False       False   
1  34.04554 -118.25667    90014           31           False       False   

   is_visible  station_id open_time close_time  ...           coordinates  \
0       False        3005  05:45:00   05:39:00  ...  (34.0485, -118.2585)   
1       False        3006  05:45:00   05:39:00  ...  (34.0455, -118.2567)   

               hex                                  hex_and_neighbors  \
0  8929a1d62cbffff  [8929a1d62cfffff, 8929a1d62c3ffff, 8929a1d62db...   
1  8929a1d75afffff  [8929a1d62dbffff, 8929a1d75abffff, 8929a1d75a7...   

   sustenance_poi  public_transport_poi education_poi arts_and_culture_poi  \
0              80                    34             1                    1   
1             102                    59             0                    5   

  sports_poi  incoming_trips  outgoing_trips  
0          5           13352           14202  
1          6            6309            6574  

[2 rows x 25 columns]

In [30]:
# plot a map with hexagons depicting the demand (i.e. the number of started trips)
variable = "outgoing_trips"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "demand"},
    range_color=(0, hexagons_df[variable].quantile(0.9)),
    palette="greens",
)
fig.show()

AttributeError: module 'H3_Visualization' has no attribute 'plot_frequency'

### Visualising points of interest
In this section we will visualize the distribution of points of interest in Los Angeles for the following categories:
- sustenance
- public transport
- education
- arts and culture
- sports

In [ ]:
variable = "sustenance_poi"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "sustenance"},
    range_color=(0, hexagons_df[variable].max()),
    palette="greens",
)
fig.show()

In [ ]:
variable = "public_transport_poi"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "public transport"},
    range_color=(0, hexagons_df[variable].max()),
    palette="reds",
)
fig.show()

In [ ]:
variable = "education_poi"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "education"},
    range_color=(0, hexagons_df[variable].max()),
    palette="blues",
)
fig.show()

In [ ]:
variable = "arts_and_culture_poi"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "arts & culture"},
    range_color=(0, hexagons_df[variable].max()),
    palette="oranges",
)
fig.show()

In [ ]:
variable = "sports_poi"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "sports"},
    range_color=(0, hexagons_df[variable].max()),
    palette="purples",
)
fig.show()

From these maps, we can see a certain similarity between the distribution of sustenance and public transport pois. Also, arts and culture and sports exhibit a particular hotspot in southeast central LA when compared to other pois. Education pois have considerably different distribution to all other categories. Sustenance and public transport seem to have good overlapping with demand map. However, these are only subjective visual observations. In the next step, we will explore the relationship between pois and demand using scientific methods.

### Correlation between different points of interest and demand
In this section, we will determine the magnitude of the correlation between the demand in different bike stations and the number of points of interest in different categories in that area.

In [ ]:
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import StandardScaler

In [ ]:
# determine input features and predicted variable for the regression
input_features = stations_df[
    [
        "sustenance_poi",
        "public_transport_poi",
        "education_poi",
        "arts_and_culture_poi",
        "sports_poi",
    ]
]
predicted_variable = stations_df["outgoing_trips"]

In [ ]:
# scale input features
scaler = StandardScaler()
input_features_scaled = scaler.fit_transform(input_features)

In [ ]:
# fit data to the linear regression model
reg = LinearRegression().fit(input_features_scaled, predicted_variable)
reg.score(input_features_scaled, predicted_variable)

The regression score (also the coefficient of determination or R^2) indicates how well selected input features explain the predicted feature. More specifically, it shows what proportion of the variance in the independent variable can be explained by dependent variables. The result of 0.59 suggests that other input variables are missing to describe demand more accurately.

In [ ]:
reg.coef_

From the regression coefficients, we see that points of interest in the category sustenance have the highest influence on the demand, followed by public transport. Interestingly though, there seems to be a small but negative effect from the education category on bike demand.

### Spatio-temporal demand patterns
Additionally, we are interested which areas are most popular to start and end trips in. This information is very useful to fleet operations, which plan and coordinate bikes relocations, to meet the highest demand.

In [ ]:
# calculate trips difference for each hexagon
hexagons_df["trips_difference"] = (
    hexagons_df["incoming_trips"] - hexagons_df["outgoing_trips"]
)

In [ ]:
# plot trips difference for each hexagon
variable = "trips_difference"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "trips difference"},
    range_color=(
        -hexagons_df[variable].quantile(0.9),
        hexagons_df[variable].quantile(0.9),
    ),
)
fig.show()

This map shows areas where more trips are ended than started (red areas) and vice versa where more trips are started than ended (blue areas). Intuitively, we would expect all hexagons to be white due to the balance of demand and supply. However, relocations are made by the bike-sharing provider to satisfy higher demand in total. Therefore, it is possible that in one area more trips are started than ended. The additional bicycles are supplied by Metro Bike Share in this case.

Next, we are interested in trip differences during specific times, like rush hours in the morning and evening.

In [ ]:
# this function will return the number of trips between the given hours and for the given 'group by' value
def calculate_hexagon_trips_by_hours(label, group_by, hours):
    hexagons_df[label] = (
        trips_df[
            (trips_df["start_time"].dt.hour >= hours[0])
            & (trips_df["start_time"].dt.hour <= hours[1])
        ]
        .groupby(group_by)
        .size()
    )
    hexagons_df[label] = hexagons_df[label].fillna(value=0)

In [ ]:
# calculate incoming and outgoing trip differences in the morning (06:00-12:00) and evening (14:00-20:00)
# (values selected based on temporal demand patterns)
# and the difference between incoming and outgoing trips in the morning and evening
hexagons_df = hexagons_df.set_index("hex")
now = datetime.now()
morning_hours = [now.replace(hour=6).hour, now.replace(hour=12).hour]
evening_hours = [now.replace(hour=14).hour, now.replace(hour=20).hour]

calculate_hexagon_trips_by_hours(
    label="incoming_trips_morning", group_by="start_hex", hours=morning_hours
)
calculate_hexagon_trips_by_hours(
    label="outgoing_trips_morning", group_by="end_hex", hours=morning_hours
)
calculate_hexagon_trips_by_hours(
    label="incoming_trips_evening", group_by="start_hex", hours=evening_hours
)
calculate_hexagon_trips_by_hours(
    label="outgoing_trips_evening", group_by="end_hex", hours=evening_hours
)

hexagons_df["trips_difference_morning"] = (
    hexagons_df["incoming_trips_morning"] - hexagons_df["outgoing_trips_morning"]
)
hexagons_df["trips_difference_evening"] = (
    hexagons_df["incoming_trips_evening"] - hexagons_df["outgoing_trips_evening"]
)

hexagons_df = hexagons_df.reset_index()
hexagons_df.head(2)

In [ ]:
# plot a map with hexagons depicting the difference between incoming and outgoing trips in the morning
variable = "trips_difference_morning"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "trips diff. morning"},
    range_color=(
        -hexagons_df[variable].quantile(0.9),
        hexagons_df[variable].quantile(0.9),
    ),
)
fig.show()

In [ ]:
# plot a map with hexagons depicting the difference between incoming and outgoing trips in the evening
variable = "trips_difference_evening"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "trips diff. evening"},
    range_color=(
        -hexagons_df[variable].quantile(0.9),
        hexagons_df[variable].quantile(0.9),
    ),
)
fig.show()

When comparing both maps, we can identify places with exactly opposite demand in the morning and evening (hexagons with different colors), for example in central LA. We also see whether the magnitude of demand is similar or not based on the intensity of colors. Additionally, we can recognize potential problematic areas, that do not balance out throughout the day. For example, one of the most north hexagons in Santa Monica always shows higher demand than the supply of bikes. This means such area requires particular attention and regular relocations.